In [4]:
import numpy as np
import matplotlib.pyplot as plt
import csv, datetime, random
import matplotlib.dates as mdates

def MakeDataFromText(filepath):
    """
    Helper function to parse text files in IFM proprietary format.
    """
    with open(filepath, 'r') as file:
        reader = csv.reader(file)

        db = dict()                          # Dictionary that will hold k,v pairs of 
        recent_EPC = ''                      # The most recent EPC that was read, and data is being assigned to
        Time_Or_Data = True                  # Time is true, Data is false
        reached_24 = False

        for l in reader:                     # Iterate over entire text file
            line = l[0]                      # Each line only has one token, so we select it
            
            if len(line)==24:                # If it is an EPC
                db[line] = [[],[]]           # Create new k,v pair in database
                recent_EPC = line            # Current EPC to add to is selected
            
            elif line == '[':                # If start bracket, beginning to collect an array of data
                data = []

            elif line == ']':                # End bracket means end of data array
                if len(data)!=0:
                    if Time_Or_Data:
                        db[recent_EPC][0] = data
                        Time_Or_Data = False
                    else:
                        db[recent_EPC][1] = data
                        Time_Or_Data = True
                data = []

            # elif len(line)==8:               # If it is a time stamp
            elif line.count(":")==2:
                h,m,s = line.split(':')      # Parse timestamp into hours, minutes, seconds

                if int(h)==23:
                    reached_24 = True        # If end of day reached, must move to Day 2

                if reached_24 and int(h) < 12:
                    day=2
                else:
                    day=1

                data.append(datetime.datetime(1970, 2, day, int(h), int(m), int(s)))
            
            elif line ==' ':               # If blank space, then we skip to parse next line
                pass

            else:                          # If it is a data point
                try:
                    data.append(float(line))
                except:
                    pass                   # Error catching case just in case, so annoying errors don't crash program
    return db


t1 = MakeDataFromText("tags after calibration 040423.txt") # PUT CSV OR TEXT FILE HERE

combined = dict()
for d in [ t1 ]:
    for k,v in d.items():
        if k in combined: # if tag is already in dict
            for i in range(len(v[0])):
                if v[0][i] in combined[k]:
                    combined[k][v[0][i]].append(v[1][i])
                else:
                    combined[k][v[0][i]] = [v[1][i]]
        else:             # if tag is not in dict
            combined[k] = dict()
            for i in range(len(v[0])):
                combined[k][v[0][i]] = [v[1][i]]
for k,v in combined.items():
    for k2,v2 in v.items():
        combined[k][k2] = sum(v2)/len(v2)

466962657264656265616B34
[
17:05:22
17:05:22
17:05:23
17:05:25
17:05:26
17:05:27
17:05:28
17:05:32
17:05:33
17:05:33
17:05:34
17:05:35
17:05:38
17:05:38
17:05:40
17:05:41
17:05:44
17:05:44
17:05:48
17:05:49
17:05:49
17:05:50
17:05:54
17:05:55
17:05:55
17:05:56
17:05:59
17:05:59
17:06:00
17:06:01
17:06:01
17:06:05
17:06:06
17:06:09
17:06:10
17:06:14
17:06:16
17:06:16
17:06:18
17:06:20
17:06:20
17:06:21
17:06:22
17:06:27
17:06:30
17:06:31
17:06:31
17:06:35
17:06:37
17:06:37
17:06:39
17:06:41
17:06:42
17:06:42
17:06:43
17:06:44
17:06:48
17:06:48
17:06:51
17:06:51
17:06:52
17:06:56
17:06:58
17:06:59
17:07:00
17:07:05
17:07:08
17:07:09
17:07:09
17:07:12
17:07:13
17:07:17
17:07:19
17:07:19
17:07:20
17:07:21
17:07:25
17:07:26
17:07:27
17:07:29
17:07:30
17:07:33
17:07:35
17:07:36
17:07:39
17:07:40
17:07:41
17:07:41
17:07:43
17:07:46
17:07:46
17:07:47
17:07:51
17:07:51
17:07:52
17:07:54
17:07:56
17:08:00
17:08:02
17:08:02
17:08:02
17:08:03
17:08:07
17:08:07
17:08:08
17:08:08
17:08:12
17:08:12
1

In [5]:
import pandas as pd

EPC_LIST = [
    # "4813", "2791", "1F7A", "6F4A", "2383", "2F66", "2E5C", "926A", "2E56", "158F", "5B06", "B28A", "73C6", "819C"
] # PUT THE EPCS YOU WANT IN THE CSV HERE AS A LIST OF STRING

list_dfs = []

for epc in EPC_LIST: # FOR EACH EPC IN THE DESIRED EPC LIST

    for k,v in combined.items():           # For each EPC in all the readings
        if k[-4:]==epc:                    # If we have the right body part
            s = sorted( v.items() )
            # time = [ j[0] for j in s if j[0]>datetime.datetime(1970, 2, 1, 7, 50, 0) and j[0]<datetime.datetime(1970, 2, 1, 8, 20, 0) ]
            # data = [ j[1] for j in s if j[0]>datetime.datetime(1970, 2, 1, 7, 50, 0) and j[0]<datetime.datetime(1970, 2, 1, 8, 20, 0) ]
            time, data = [ j[0] for j in s ], [ j[1] for j in s ]

            small_df = pd.DataFrame(
                data = {'Datetime':time, epc:data},
                columns=['Datetime', epc]
            )
            list_dfs.append(small_df)


all_data = pd.concat([t for t in list_dfs], ignore_index=False)
all_data = all_data.set_index('Datetime')
all_data = all_data.sort_index()
all_data = all_data.groupby(level=0).sum()
all_data = all_data.groupby(all_data.index).sum()
all_data = all_data.replace(0, "-")
all_data.to_excel("tags_after_calibration_040423.xlsx") # CHANGE THE NAME OF OUTPUT FILE HERE

ValueError: No objects to concatenate